<img src='https://encrypted-tbn0.gstatic.com/images?q=tbn%3AANd9GcQ-VfNtOyJbsaxu43Kztf_cv1mgBG6ZIQZEVw&usqp=CAU'>

# Procesamiento de Lenguaje Natural

## Proyecto Final 2020-II

## Presentado por: Juan Sebastian Cruz Dionicio


# Análisis de 69 pequeñas historias de Edgar Allan Poe

## Objetivos 

### Entender las palabras mas usadas y su relación en los diferentes escritos

### Analizar las historias de Edgar Allan Poe, mediante la visualización de las diferentes temáticas

### Obtener mediante un modelo Machine Learning un cuento corto usando como base las otras 69 historias. 

### Cargue de librerias iniciales 

In [1]:
import re
import numpy as np
import pandas as pd
import os


from nltk.corpus import stopwords
stopwords_sp = stopwords.words('english')
from nltk.stem.snowball import SnowballStemmer
spanishStemmer=SnowballStemmer("english")

#Word2vec
from nltk.corpus import stopwords
import gensim.models.word2vec as w2v
stopwords_sp = stopwords.words('english')
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

#Librerias para poder visualizar 
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import plotly.graph_objs as go
from plotly.offline import iplot

#Modelado de temas
import re
import pandas as pd 
from pprint import pprint
import pyLDAvis.gensim
from gensim.models import LdaModel
from gensim.corpora import Dictionary
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)


In [2]:
#Redes Neuronales
from __future__ import absolute_import, division, print_function, unicode_literals

import os
import re
import time
import tensorflow as tf

In [3]:
os.getcwd()
df = pd.read_csv("preprocessed_data.csv", sep=",")
df.head(10)

title  \
0             A DESCENT INTO THE MAELSTRÖM   
1                            A PREDICAMENT   
2                      A TALE OF JERUSALEM   
3           A TALE OF THE RAGGED MOUNTAINS   
4                                 BERENICE   
5                                 DIDDLING   
6                                 ELEONORA   
7  FOUR BEASTS IN ONE—THE HOMO-CAMELEOPARD   
8                                 HOP-FROG   
9         HOW TO WRITE A BLACKWOOD ARTICLE   

                                                text  \
0  The ways of God in Nature, as in Providence, a...   
1  What chance, good lady, hath bereft you thus? ...   
2  Intensos rigidarn in frontern ascendere canos ...   
3  DURING the fall of the year 1827, while residi...   
4  Dicebant mihi sodales, si sepulchrum amicae vi...   
5  CONSIDERED AS ONE OF THE EXACT SCIENCES.    He...   
6  Sub conservatione formae specificae salva anim...   
7  Chacun a ses vertus. —Crebillon’s Xerxes.  ANT...   
8  I never knew anyone so keenly alive to a joke ...   
9  “In the name of the Prophet—figs!!” Cry of the...   

                           wikipedia_title  publication_date  \
0             A Descent into the Maelström          May 1841   
1                            A Predicament     November 1838   
2                      A Tale of Jerusalem      June 9, 1832   
3           A Tale of the Ragged Mountains        April 1844   
4                                 Berenice        March 1835   
5                                 Diddling  October 14, 1843   
6                                 Eleonora            ? 1841   
7  Four Beasts in One—The Homo-Cameleopard        March 1836   
8                                 Hop-Frog    March 17, 1849   
9         How to Write a Blackwood Article     November 1838   

              first_published_in             classification  \
0              Graham's Magazine                  Adventure   
1      Baltimore American Museum                     Parody   
2  Philadelphia Saturday Courier                      Humor   
3            Godey's Lady's Book  Adventure,Science_fiction   
4    Southern Literary Messenger                     Horror   
5  Philadelphia Saturday Courier                     Parody   
6              The Gift for 1842                    Romance   
7    Southern Literary Messenger                      Humor   
8              Flag of Our Union                     Horror   
9      Baltimore American Museum                     Parody   

                                               notes normalized_date  
0                                                  ?        May 1841  
1  Companion to "How to Write a Blackwood Article...   November 1838  
2                                                  ?       June 1832  
3                                                  ?      April 1844  
4                                                  ?      March 1835  
5  Originally "Raising the Wind; or, Diddling Con...    October 1843  
6                                                  ?          ? 1841  
7                              Originally "Epimanes"      March 1836  
8   Subtitled "Or, The Eight Chained Ourang-Outangs"      March 1849  
9                 An introduction to "A Predicament"   November 1838

### Pre-procesamiento de los datos 

In [4]:
def pre_procesado(texto):
    texto = texto.lower()
    texto = re.sub(r"[\W\d_]+", " ", texto)
    texto = " ".join([palabra for palabra in texto.split() if palabra not in stopwords_sp])
    return texto

In [5]:
df['pre-procesado'] = df['text'].apply(lambda texto: pre_procesado(texto))
df

title  \
0                    A DESCENT INTO THE MAELSTRÖM   
1                                   A PREDICAMENT   
2                             A TALE OF JERUSALEM   
3                  A TALE OF THE RAGGED MOUNTAINS   
4                                        BERENICE   
..                                            ...   
65                               THE BALLOON-HOAX   
66                     THE MYSTERY OF MARIE ROGET   
67                           THE POETIC PRINCIPLE   
68  THE UNPARALLELED ADVENTURES OF ONE HANS PFAAL   
69                              X-ING A PARAGRAPH   

                                                 text  \
0   The ways of God in Nature, as in Providence, a...   
1   What chance, good lady, hath bereft you thus? ...   
2   Intensos rigidarn in frontern ascendere canos ...   
3   DURING the fall of the year 1827, while residi...   
4   Dicebant mihi sodales, si sepulchrum amicae vi...   
..                                                ...   
65  [Astounding News by Express, via Norfolk!—The ...   
66  A SEQUEL TO “THE MURDERS IN THE RUE MORGUE.”  ...   
67  IN speaking of the Poetic Principle, I have no...   
68  BY late accounts from Rotterdam, that city see...   
69  AS it is well known that the ‘wise men’ came ‘...   

                   wikipedia_title publication_date  \
0     A Descent into the Maelström         May 1841   
1                    A Predicament    November 1838   
2              A Tale of Jerusalem     June 9, 1832   
3   A Tale of the Ragged Mountains       April 1844   
4                         Berenice       March 1835   
..                             ...              ...   
65                               ?   April 13, 1844   
66                               ?    November 1842   
67                               ?  August 17, 1849   
68                               ?        June 1835   
69                               ?     May 12, 1849   

               first_published_in             classification  \
0               Graham's Magazine                  Adventure   
1       Baltimore American Museum                     Parody   
2   Philadelphia Saturday Courier                      Humor   
3             Godey's Lady's Book  Adventure,Science_fiction   
4     Southern Literary Messenger                     Horror   
..                            ...                        ...   
65                              ?               Fiction,Hoax   
66                              ?          Detective_fiction   
67                              ?                      Essay   
68                              ?       Hoax,Science_fiction   
69                              ?                     Satire   

                                                notes normalized_date  \
0                                                   ?        May 1841   
1   Companion to "How to Write a Blackwood Article...   November 1838   
2                                                   ?       June 1832   
3                                                   ?      April 1844   
4                                                   ?      March 1835   
..                                                ...             ...   
65                                                  ?      April 1844   
66                                                  ?   November 1842   
67                                                  ?     August 1849   
68                                                  ?       June 1835   
69                                                  ?        May 1849   

                                        pre-procesado  
0   ways god nature providence ways models frame w...  
1   chance good lady hath bereft thus comus quiet ...  
2   intensos rigidarn frontern ascendere canos pas...  
3   fall year residing near charlottesville virgin...  
4   dicebant mihi sodales si sepulchrum amicae vis...  
..                                                ...  
65  astounding news exp

In [6]:
test = df.groupby(['classification']) ['title'].count()
test

classification
Adventure                       3
Adventure,Science_fiction       1
Detective_fiction               3
Detective_fiction,Satire        1
Essay                           4
Fantasy                         1
Fantasy,Horror                  1
Fiction,Hoax                    1
Hoax,Horror,Science_fiction     1
Hoax,Satire                     1
Hoax,Science_fiction            2
Horror                         17
Horror,Humor                    1
Horror,Ratiocination            1
Horror,Satire                   1
Humor                          13
Humor,Satire                    1
Parody                          3
Romance                         1
Satire                          6
Science_fiction                 4
Sketch                          3
Name: title, dtype: int64

## Modelo Word2Vec

Encontrar como estan distribuidas las palabras y como pueden estar relacionadas a lo largo de los 69 cuentos de Edgar Allan Poe. 

Nuevamente se correra una función para arreglar la data ya que la función recibe los datos en otro formato. 

In [7]:
def pre_procesado(texto):

     texto = texto.lower()
     texto = re.sub(r"[\W\d_]+", " ", texto)
     texto = " ".join([palabra for palabra in texto.split() if palabra not in stopwords_sp])
     return texto.split()

df['word2vec'] = df['pre-procesado'].apply(lambda texto: pre_procesado(texto))
df.head()

title  \
0    A DESCENT INTO THE MAELSTRÖM   
1                   A PREDICAMENT   
2             A TALE OF JERUSALEM   
3  A TALE OF THE RAGGED MOUNTAINS   
4                        BERENICE   

                                                text  \
0  The ways of God in Nature, as in Providence, a...   
1  What chance, good lady, hath bereft you thus? ...   
2  Intensos rigidarn in frontern ascendere canos ...   
3  DURING the fall of the year 1827, while residi...   
4  Dicebant mihi sodales, si sepulchrum amicae vi...   

                  wikipedia_title publication_date  \
0    A Descent into the Maelström         May 1841   
1                   A Predicament    November 1838   
2             A Tale of Jerusalem     June 9, 1832   
3  A Tale of the Ragged Mountains       April 1844   
4                        Berenice       March 1835   

              first_published_in             classification  \
0              Graham's Magazine                  Adventure   
1      Baltimore American Museum                     Parody   
2  Philadelphia Saturday Courier                      Humor   
3            Godey's Lady's Book  Adventure,Science_fiction   
4    Southern Literary Messenger                     Horror   

                                               notes normalized_date  \
0                                                  ?        May 1841   
1  Companion to "How to Write a Blackwood Article...   November 1838   
2                                                  ?       June 1832   
3                                                  ?      April 1844   
4                                                  ?      March 1835   

                                       pre-procesado  \
0  ways god nature providence ways models frame w...   
1  chance good lady hath bereft thus comus quiet ...   
2  intensos rigidarn frontern ascendere canos pas...   
3  fall year residing near charlottesville virgin...   
4  dicebant mihi sodales si sepulchrum amicae vis...   

                                            word2vec  
0  [ways, god, nature, providence, ways, models, ...  
1  [chance, good, lady, hath, bereft, thus, comus...  
2  [intensos, rigidarn, frontern, ascendere, cano...  
3  [fall, year, residing, near, charlottesville, ...  
4  [dicebant, mihi, sodales, si, sepulchrum, amic...

In [8]:
# Creando mi modelo de word2vec
 
mi_modelo = w2v.Word2Vec(df['word2vec'].values,

                          sg=1, # 1 skip-gram. 0 CBOW

                          seed=1, # semilla

                          size=256, # número de dimensiones

                          min_count=50,

                          window=12)

In [9]:
#Prueba del Modelo 
vocab = [e[0] for e in mi_modelo.wv.most_similar("love")]

print(vocab)

['spirit', 'thou', 'heart', 'soul', 'feel', 'strange', 'memory', 'world', 'yet', 'heaven']


In [10]:
#Prueba del Modelo 
vocab = [e[0] for e in mi_modelo.wv.most_similar("dark")]

print(vocab)

['night', 'evening', 'dead', 'remained', 'passed', 'forth', 'away', 'breath', 'bed', 'arrived']


In [11]:
X = mi_modelo[mi_modelo.wv.vocab]

matrix = pd.DataFrame(X)

matrix.index = mi_modelo.wv.vocab.keys()
 
matrix

0         1         2         3         4         5    \
god       -0.014711 -0.046355  0.124250 -0.082814  0.002328  0.208728   
nature    -0.119244  0.019640  0.103022  0.046367 -0.000686  0.121463   
way       -0.038525  0.017844  0.107376 -0.059498  0.042847 -0.021166   
greater   -0.157732  0.110346  0.095507 -0.006267 -0.011882 -0.008842   
well      -0.070601  0.021097  0.114798 -0.013057  0.021555  0.018869   
...             ...       ...       ...       ...       ...       ...   
poem      -0.208816  0.016434  0.133397  0.107244 -0.028413  0.150050   
monsieur   0.026487  0.088783  0.274370 -0.137635 -0.057845  0.007832   
dupin      0.020716 -0.005943  0.168911  0.031050  0.022870  0.038481   
marie      0.091317 -0.010838  0.067007  0.007257 -0.034806 -0.104002   
automaton  0.015677  0.012525  0.012814  0.017189  0.043892 -0.025787   

                6         7         8         9    ...       246       247  \
god       -0.173810 -0.041145  0.021389 -0.219900  ...  0.006548 -0.225709   
nature    -0.134456  0.004699 -0.012700 -0.149956  ...  0.030030 -0.110049   
way       -0.048739 -0.097542 -0.136362 -0.028595  ...  0.083848 -0.126042   
greater   -0.050704 -0.090520 -0.038033 -0.125390  ... -0.017303 -0.115988   
well      -0.084525 -0.095176 -0.078157 -0.060496  ...  0.012351 -0.119727   
...             ...       ...       ...       ...  ...       ...       ...   
poem      -0.209620  0.014697 -0.065657 -0.168671  ...  0.049120 -0.108067   
monsieur  -0.123955 -0.135940 -0.110473  0.021325  ... -0.016785 -0.198264   
dupin     -0.187508 -0.029807 -0.142977 -0.018391  ...  0.008739 -0.170425   
marie     -0.130185 -0.128694 -0.088021  0.171805  ... -0.083539 -0.176582   
automaton -0.043562 -0.086216 -0.108988 -0.145052  ...  0.201178 -0.162744   

                248       249       250       251       252       253  \
god        0.065760  0.093904  0.151252 -0.189449 -0.124080  0.034079   
nature     0.071065  0.004389  0.114458 -0.131479 -0.073465  0.037547   
way        0.078665 -0.025404  0.031986 -0.098509  0.023976  0.056529   
greater    0.034250  0.014503  0.071816 -0.154372 -0.082916  0.064794   
well       0.066039 -0.005357  0.022434 -0.148129 -0.039626  0.063791   
...             ...       ...       ...       ...       ...       ...   
poem       0.151213  0.025506  0.131728 -0.227701 -0.114097  0.006529   
monsieur   0.096693  0.001191 -0.065926 -0.220568 -0.147162 -0.005128   
dupin      0.137673 -0.021376 -0.027641 -0.166774 -0.119381 -0.010691   
marie      0.075905 -0.010284 -0.082781 -0.242017 -0.202834  0.052359   
automaton -0.013423 -0.035458  0.088095  0.024345  0.117631  0.055011   

                254       255  
god        0.040703  0.191948  
nature     0.016353  0.189183  
way        0.096492  0.114409  
greater    0.096680  0.105010  
well       0.114040  0.090514  
...             ...       ...  
poem       0.019310  0.113130  
monsieur   0.252946  0.119256  
dupin      0.111203  0.110422  
marie      0.213008  0.184626  
automaton  0.015215  0.302648  

[545 rows x 256 columns]

In [12]:
pca = PCA(n_components=2)
 
result = pca.fit_transform(matrix)

result = pd.DataFrame(result)

result.columns = ['X', 'Y']

result['Palabra'] = matrix.index.values
 
result

X         Y    Palabra
0    0.732634  0.710312        god
1    0.585040  0.697340     nature
2    0.154141 -0.451707        way
3    0.054148  0.299435    greater
4    0.482582 -0.172112       well
..        ...       ...        ...
540  1.272457  0.805626       poem
541  0.530902 -0.770315   monsieur
542  0.873310 -0.406496      dupin
543  0.422644 -0.627673      marie
544 -0.244406 -0.347882  automaton

[545 rows x 3 columns]

In [13]:
trace = go.Scatter(x=result['X'].values,

                    y=result['Y'].values,

                    text=result['Palabra'].values,

                    mode='markers') 
 
layout = go.Layout(title="PCA")
fig = go.Figure(data=trace, layout=layout)
iplot(fig)

## Modelado de temas 

Una vez vista la relación de las palabras con nuestro modelo de Word2vec, haremos un modelo para poder apreciar el modelado de temas de los cuentos de Edgar Allan Poe haciendo uso de un modelo de LDA.

import re
import pandas as pd 
from pprint import pprint

from nltk.corpus import stopwords
stopwords_sp = stopwords.words('english')

import pyLDAvis.gensim
from gensim.models import LdaModel
from gensim.corpora import Dictionary

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

In [14]:
# Crear una representación de los documentos en forma de diccionario
dictionary = Dictionary(df['word2vec'].values)


# Filtrar palabras muy frecuentes o infrecuentes
dictionary.filter_extremes(no_below=5, no_above=0.5)
 
corpus = [dictionary.doc2bow(text) for text in df['word2vec'].values]


#Train the topic model
model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=5, passes=200)

In [15]:
lda_display = pyLDAvis.gensim.prepare(model, corpus, dictionary, sort_topics=True)

pyLDAvis.display(lda_display)

C:\Users\Sebastian Cruz\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




## Modelo de Redes Neuronales 


from __future__ import absolute_import, division, print_function, unicode_literals

import os
import re
import time
import numpy as np
import pandas as pd
import tensorflow as tf

In [16]:
text = df.text.str.cat(sep=" ")
text

'The ways of God in Nature, as in Providence, are not as our ways; nor are the models that we frame any way commensurate to the vastness, profundity, and unsearchableness of His works, which have a depth in them greater than the well of Democritus. Joseph Glanville.    WE had now reached the summit of the loftiest crag. For some minutes the old man seemed too much exhausted to speak.     “Not long ago,” said he at length, “and I could have guided you on this route as well as the youngest of my sons; but, about three years past, there happened to me an event such as never happened to mortal man—or at least such as no man ever survived to tell of—and the six hours of deadly terror which I then endured have broken me up body and soul. You suppose me a very old man—but I am not. It took less than a single day to change these hairs from a jetty black to white, to weaken my limbs, and to unstring my nerves, so that I tremble at the least exertion, and am frightened at a shadow. Do you know I

In [17]:
vocab = sorted(set(text))
print(f'{len(vocab):,.0f} caracteres únicos')
char2idx = {u:i for i, u in enumerate(vocab)}
idx2char = np.array(vocab)
# Traducir nuestro texto a números
text_as_int = np.array([char2idx[c] for c in text])

102 caracteres únicos


In [18]:
seq_length = 100
# Crear el conjunto de datos de entrenamiento
char_dataset = tf.data.Dataset.from_tensor_slices(text_as_int)
sequences = char_dataset.batch(seq_length+1, drop_remainder=True)

In [19]:
def split_input_target(chunk):
    input_text = chunk[:-1]
    target_text = chunk[1:]
    return input_text, target_text

dataset = sequences.map(split_input_target)

In [20]:
for i,(input_example, target_example) in  enumerate(dataset.take(1)):
    print('Input data: ', repr(''.join(idx2char[input_example.numpy()])))
    print('Target data:', repr(''.join(idx2char[target_example.numpy()])))

Input data:  'The ways of God in Nature, as in Providence, are not as our ways; nor are the models that we frame a'
Target data: 'he ways of God in Nature, as in Providence, are not as our ways; nor are the models that we frame an'


In [21]:
for i, (input_idx, target_idx) in enumerate(zip(input_example[:5], target_example[:5])):
    print(f"Paso {i}")
    print(f"  input: {input_idx} ({repr(idx2char[input_idx])})")
    print(f"  expected output: {target_idx} ({repr(idx2char[target_idx])})")
    print()

Paso 0
  input: 45 ('T')
  expected output: 61 ('h')

Paso 1
  input: 61 ('h')
  expected output: 58 ('e')

Paso 2
  input: 58 ('e')
  expected output: 0 (' ')

Paso 3
  input: 0 (' ')
  expected output: 76 ('w')

Paso 4
  input: 76 ('w')
  expected output: 54 ('a')



In [22]:
#Creando lotes de entrenamiento
BATCH_SIZE = 256

BUFFER_SIZE = 10000

dataset = dataset.shuffle(BUFFER_SIZE).batch(BATCH_SIZE, drop_remainder=True)

dataset

<BatchDataset shapes: ((256, 100), (256, 100)), types: (tf.int32, tf.int32)>

In [23]:
# Length of the vocabulary in chars
vocab_size = len(vocab)

# The embedding dimension
embedding_dim = 64

# Number of RNN units
rnn_units = 512

In [24]:
def build_model(vocab_size, embedding_dim, rnn_units, batch_size):
    model = tf.keras.Sequential([
    tf.keras.layers.Embedding(vocab_size, embedding_dim,
                              batch_input_shape=[batch_size, None]),
    tf.keras.layers.GRU(rnn_units,
                        return_sequences=True,
                        stateful=True,
                        recurrent_initializer='glorot_uniform'),
    tf.keras.layers.GRU(rnn_units,
                        return_sequences=True,
                        stateful=True,
                        recurrent_initializer='glorot_uniform'),
    tf.keras.layers.Dense(vocab_size)
  ])
    return model

In [25]:
model = build_model(
    vocab_size = len(vocab),
    embedding_dim=embedding_dim,
    rnn_units=rnn_units,
    batch_size=BATCH_SIZE)

model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (256, None, 64)           6528      
_________________________________________________________________
gru (GRU)                    (256, None, 512)          887808    
_________________________________________________________________
gru_1 (GRU)                  (256, None, 512)          1575936   
_________________________________________________________________
dense (Dense)                (256, None, 102)          52326     
Total params: 2,522,598
Trainable params: 2,522,598
Non-trainable params: 0
_________________________________________________________________


In [26]:
# Entrenamiento del Modelo
# Función de perdida para optimizar el modelo
def loss(labels, logits):
      return tf.keras.losses.sparse_categorical_crossentropy(labels, logits, from_logits=True)

In [27]:
model.compile(optimizer='adam', loss=loss)

In [28]:
# Directory where the checkpoints will be saved
checkpoint_dir = 'training_checkpoints/'
# Name of the checkpoint files
checkpoint_prefix = os.path.join(checkpoint_dir, "ckpt_{epoch}")

checkpoint_callback=tf.keras.callbacks.ModelCheckpoint(
        filepath=checkpoint_prefix,
        save_weights_only=True)

In [29]:
# Una epoca es la cantidad de pasos completos en el conjunto de datos de entrenamiento
EPOCHS=45
#model.load_weights(tf.train.latest_checkpoint(checkpoint_dir)) # Comentar esta linea la primera vez 
history = model.fit(dataset, epochs=EPOCHS, callbacks=[checkpoint_callback])

Epoch 1/45
74/74 [==============================] - 504s 7s/step - loss: 3.1821
Epoch 2/45
74/74 [==============================] - 642s 9s/step - loss: 2.5443
Epoch 3/45
74/74 [==============================] - 747s 10s/step - loss: 2.2089
Epoch 4/45
74/74 [==============================] - 760s 10s/step - loss: 1.9941
Epoch 5/45
74/74 [==============================] - 770s 10s/step - loss: 1.8298
Epoch 6/45
74/74 [==============================] - 770s 10s/step - loss: 1.7033
Epoch 7/45
74/74 [==============================] - 793s 11s/step - loss: 1.6060
Epoch 8/45
74/74 [==============================] - 798s 11s/step - loss: 1.5309
Epoch 9/45
74/74 [==============================] - 787s 11s/step - loss: 1.4728
Epoch 10/45
74/74 [==============================] - 793s 11s/step - loss: 1.4281
Epoch 11/45
74/74 [==============================] - 786s 11s/step - loss: 1.3914
Epoch 12/45
74/74 [==============================] - 747s 10s/step - loss: 1.3610
Epoch 13/45
74/74 [========

In [30]:
p_model = build_model(vocab_size, embedding_dim, rnn_units, batch_size=1)
p_model.load_weights(tf.train.latest_checkpoint(checkpoint_dir))
p_model.build(tf.TensorShape([1, None]))

In [35]:
#Predicciones
def generate_text(model, start_string):
    # Evaluation step (generating text using the learned model)

    # Number of characters to generate
    num_generate = 500

    # Converting our start string to numbers (vectorizing)
    input_eval = [char2idx[s] for s in start_string]
    input_eval = tf.expand_dims(input_eval, 0)

    # Empty string to store our results
    text_generated = []

    # Low temperatures results in more predictable text.
    # Higher temperatures results in more surprising text.
    # Experiment to find the best setting.
    temperature = 1.0

    # Here batch size == 1
    model.reset_states()
    for i in range(num_generate):
        predictions = model(input_eval)
        # remove the batch dimension
        predictions = tf.squeeze(predictions, 0)

        # using a categorical distribution to predict the word returned by the model
        predictions = predictions / temperature
        predicted_id = tf.random.categorical(predictions, num_samples=1)[-1,0].numpy()

        # We pass the predicted word as the next input to the model
        # along with the previous hidden state
        input_eval = tf.expand_dims([predicted_id], 0)
 
        text_generated.append(idx2char[predicted_id])

    return(start_string + ''.join(text_generated))       

##### Resultado modelo con una perdida de 1.3100 y 15 Epochs 

In [111]:
#print(generate_text(p_model, start_string=u"The dark night"))

The dark night,” said such all then I re mistance all himself awower, beneding the infance. He is appeared a wiseution. Nith the Harmed result of their ear are form off and revelopmed, was no extending itself our line, and of the implicity. Yet it found into the more prominct or the room, and took the neck. Munified just and just avalogical place. The greatest interrupted smixh and the grâting courage for the always have never before any endeavor; an order account of my good; and then, who crossed by success)


### The dark night: (Español) 


"La noche oscura", dijo todo eso y luego me quedé asombrado, bendiciendo a la infanta. Parece un sabio. Nith el resultado dañado de su oído se forma y se reurbaniza, no se extendía nuestra línea, y de la implicidad. Sin embargo, encontró el más prominente de la habitación y tomó el cuello. Munificado un lugar justo y valioso. El mayor smixh interrumpido y el gran coraje para siempre nunca antes han tenido ningún esfuerzo; una cuenta de orden de mi bien; y luego, quien atravesó el éxito.

##### Resultado modelo con una perdida de 0.9444 y 45 Epochs 

In [36]:
print(generate_text(p_model, start_string=u"The dark night"))

The dark nighty-day in the effect of this nature leaping, merely aroused by the Seine, there were two, nivelled in the less extra step of the dim mothat the tromb of the Rue Caval incistant was a species of marging is not the betrace of myself within the gloom, and frankly complice had filled me bound for miles and water, of writing myself, and denorious thousand fiends, and becall away from haming Ashaps, made them so in spigabied, finally made a great individual instances of light minute and equitor, very s


### The dark night: (Español) 


El oscuro día nocturno en el efecto de esta naturaleza saltando, simplemente despertado por el Sena, había dos, nivelado en el paso menos extra de la tenue mota que el trombo de la Rue Caval incistant era una especie de marginación no es la traición de Yo mismo en la penumbra, y francamente elogio me había llenado con destino a millas y agua, de escribirme a mí mismo, y a miles de demonios denorios, y lejos de molestar a Ashaps, los hizo tan en forma, finalmente hizo una gran instancia individual de luz minuto y equitoria.